Kristen Swerzenski

DSC 540

18 February 2024

## Project Milestone 4: Cleaning and Formatting API Data

### Introduction

For my API, I chose to pull data from The Movie Database (TMDb) API to fill in some extra details on movies that I have data on from my other sources (budget, genres, user ratings, etc.). Because our ultimate goal will be to combine our three data sources by using a common key, and to be mindful of the number of requests that I am sending to the API, I am going to pull data on film titles that appear in both of my previous data sets so far. To do that I will begin by reading in the titles from my two previously cleaned and saved .csv files and get a list of common titles between the two which I will then loop into calls to the API. 

In [1]:
# Importing necessary packages
import json
import requests
import csv
import pandas as pd
from pandas import json_normalize
import numpy as np

In [2]:
# Setting pandas display settings to view all data
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)

In [3]:
# Defining a function to read titles from my previous data sets
def read_movie_titles(filename):
    # Creating an empty set to store titles
    titles = set()
    # Opening and reading the .csv file
    with open(filename, newline='', encoding='utf-8') as csvfile:
        reader = csv.DictReader(csvfile)
        # Appending the data in the title column of each row into the titles set
        for row in reader:
            titles.add(row['title'])
    return titles

# Reading the movie title data from both files
titles_file1 = read_movie_titles('boxoffice.csv')
titles_file2 = read_movie_titles('streaming_movies.csv')

# Using .intersection() to find the common titles
common_titles = titles_file1.intersection(titles_file2)

# Converting the set of common titles to a list
common_titles_list = list(common_titles)

# Printing the list of common movie titles to check it
print("Common Movie Titles:")
for title in common_titles_list:
    print(title)

Common Movie Titles:
After We Collided
Supernova
Bombshell
Leave No Trace
The Addams Family
Beirut
Crawl
Honey Boy
Den of Thieves
Hotel Transylvania 3: Summer Vacation
Save Yourselves!
The Last Full Measure
Seberg
Everybody Knows
Apollo 11
Peppermint
The Secrets We Keep
The Happytime Murders
Colette
The Wretched
2 Hearts
Possessor
The Tax Collector
Brian Banks
She Dies Tomorrow
Free Solo
Hotel Mumbai
The Hate U Give
The Secret Life of Pets 2
Echo in the Canyon
I Feel Pretty
Adrift
Honest Thief
The Resort
Beautiful Boy
The Beach Bum
The Goldfinch
Infamous
The Last Black Man in San Francisco
Bharat
The Water Man
Jathi Ratnalu
Raya and the Last Dragon
Final Account
The Assistant
Black Panther
Les Misérables
Three Identical Strangers
Samson
Midsommar
Sorry to Bother You
After
The Hunt
Bad Samaritan
Five Feet Apart
Cats
47 Meters Down: Uncaged
The Best of Enemies
Jay and Silent Bob Reboot
Pain and Glory
Ava
Wild Mountain Thyme
Spider-Man: Into the Spider-Verse
Dora and the Lost City of Gold

Now that I know what requests for what data I want to make for the API, I am going to make a clal to the API looping in that list of titles and converting the returned JSON data into a pandas data frame.

In [4]:
# Opening the API key stored in a .json file
with open('tmdbapikey.json') as f:
    api_data = json.load(f)
    API_KEY = api_data['tmdb_apikey']

# Creating a function that fetches movie data by title
def fetch_movie_details(title, api_key):
    # Building the url for the API call
    url = f'https://api.themoviedb.org/3/search/movie?query={title}&api_key={api_key}'
    # Sending a get request to the API url
    response = requests.get(url)
    # Parsing the response as JSON data
    data = response.json()
    # Returning the retrieved JSON data
    return data

# Creating a list to store JSON data from API call (will be a list of dictionaries)
common_titles_data = []

# Looping the fetch_movie_details function through all titles in the common_titles_list to get data for each of the movies
for title in common_titles_list:
    # Fetching data for a title using thr API key
    movie_data = fetch_movie_details(title, API_KEY)
    # Extending the common_titles_data list with the movie data
    common_titles_data.extend(movie_data.get('results', []))

# Converting the list of JSON data dictionaries to a pandas data frame
movie_data = pd.DataFrame(common_titles_data)

# Displaying the data frame to check it
display(movie_data)

adult                     backdrop_path  \
0     False  /6hgItrYQEG33y0I7yP2SRl2ei4w.jpg   
1     False  /przsU4aiGsdlDkCp5uV8kq8gbLe.jpg   
2     False   /BjLgTDAcZc94KomcQAxMVye0yI.jpg   
3     False                              None   
4     False  /9n46ONadB3wz2gi2R7vR5NgRAQ4.jpg   
5     False  /xK5l1CMj4HllYfgCcOngC86E4o1.jpg   
6     False                              None   
7     False                              None   
8     False  /3PGNAiILVNhIYtpge5miP2AaT3H.jpg   
9     False                              None   
10    False                              None   
11    False  /nC86jat6h6WxlQeCRyZIQAjjCsb.jpg   
12    False                              None   
13    False                              None   
14    False                              None   
15    False                              None   
16    False                              None   
17    False  /qlWUOd19T8qfzFSY5oUkppzNq24.jpg   
18    False                              None   
19    False  /xAY88MFK4avT1CkU38LyB9AVh7L.jpg   
20    False                              None   
21    False  /nj84vpuUWdbmYktBzjiWn5Ny1ZF.jpg   
22    False  /6o06tJsEqLziirSSuJt3Vk5y2KZ.jpg   
23    False  /8zZhyAiMCX5yAQill5f9AhnncuI.jpg   
24    False                              None   
25    False  /e37ZG1z8uvbo26JXfEV8gW1SBV0.jpg   
26    False                              None   
27    False                              None   
28    False  /coXMUtJqp2A81Q1gxfqJdpMSLmz.jpg   
29    False                              None   
30    False                              None   
31    False  /wHaffL9KEi8R9oXLcskztn1t0LX.jpg   
32    False  /4K7PYRGlAgoVrmbwa7SuYiBNe2O.jpg   
33    False  /obLTXoHu8UjlHjKjSwoRkgDKqaV.jpg   
34    False                              None   
35    False  /lC6gofoYMkJMhVZI7aqDDnn6AQN.jpg   
36    False                              None   
37    False                              None   
38    False  /ngg1QJuolhBK4NmNUbyRgdprlud.jpg   
39    False                              None   
40    False                              None   
41    False  /1qDDU5kQUG3NwahbrUIXJcW36wu.jpg   
42    False  /cqcA0UeUFAajsd1XSpqGfqyqQN9.jpg   
43    False  /nLR51KAM1lvyzLYnLu2gWbAPlwQ.jpg   
44    False                              None   
45    False  /xPBAIx2KggRiwaTmT7sF4CAbyVk.jpg   
46    False                              None   
47    False  /e02V5RVJqMbQQG8cLwBWom2bEXY.jpg   
48    False  /uCAy0n0WHTGU4d3LMJtE0fQxCej.jpg   
49    False  /7OxGhxUYAdtuike29VMzEFxJx7y.jpg   
50    False  /9e6wp707XMouPG939o2fHunXXJR.jpg   
51    False  /nE49wBYzM91soU7cnqypOBalxgX.jpg   
52    False  /uuXqH1CSYVWV3qbRyyaLJ74IN44.jpg   
53    False                              None   
54    False                              None   
55    False                              None   
56    False  /mamhgDI6uh7zVXQXbq1XWGFhkWs.jpg   
57    False  /yrjFk8OVnwOQ5qUxbHZJYobxQra.jpg   
58    False  /2nLOJ8gtattGzYzwlYM8PrcgknH.jpg   
59    False                              None   
60    False  /mdEptut4OxuOjEl0tMTY0fHyMNt.jpg   
61    False  /goL6SSpFDkxveXTnEvP76sGQQOz.jpg   
62    False  /mzTwGdetIZPoSDbfMEBHfLKBrQ7.jpg   
63    False  /hAUIW7OAXDuOgrvuW9mSB5end9s.jpg   
64    False                              None   
65    False  /5NmbBnYW6KUJWwRcUgtCmfHuvOr.jpg   
66    False  /e50IT4Sjd8lPpR38VQrO5uKLOwe.jpg   
67    False                              None   
68    False   /W36zPecTdW733qVGc8oSaOUYyc.jpg   
69    False  /jarPXif52Miy10tbeJwoArtR2yr.jpg   
70    False                              None   
71    False                              None   
72    False  /aknUwMbdL5BIclEkMVfdyoQHr6i.jpg   
73    False                              None   
74    False  /wtSVHEygyIvmmcaQXbET64XQ83j.jpg   
75    False                              None   
76    False                              None   
77    False                              None   
78    False  /lm4xH0YwFbVvTgdtau1thNK5S6J.jpg   
79    False  /3RkOPJUkQdfgBVgLLw4v4fNirxZ.jpg   
80    False                          

It seems like there may have been some multiple matches for certain titles and pulled in a number of different duplicate title films. I will need to make another call to the API in order to get more detailed information on the films now that I have the movie IDs, but first I am going to clean up some of the extranneous titles retrieved in order to not overload the API.

#### Step 1: Dropping all films that are not exact title matches to the titles in common_titles_list

The first thing I want to do is drop all titles that were not exact matches to the title in my common titles list. 

In [5]:
# Checking to see if title is an exact match to titles in movie_data list, dropping of not
movie_data = movie_data[movie_data['title'].isin(common_titles_list)]

# Resetting index after dropping rows
movie_data.reset_index(drop=True, inplace=True)

# Checking the length of the data frame to see if rows were dropped
len(movie_data)

493

The number of rows significantly decreased, so it seems like that worked relatively well. However, there are some duplicate films with exact title matches so I can do a little more trimming down before making the next API call.

#### Step 2: Changing release_date to datetime and removing films with release dates before 2018

Since my project is focusing on films released in 2018 or alter, I can do a little additional trimming before making another call to the API. I will first convert the release_date column to a datetime type and drop any rows with release dates before 2018.

In [6]:
# Converting release_date to datetime
movie_data['release_date'] = pd.to_datetime(movie_data['release_date'])

# Filtering rows with release dates before 2018
movie_data = movie_data[movie_data['release_date'].dt.year >= 2018]

# Resetting index after dropping rows
movie_data.reset_index(drop=True, inplace=True)

# Checking length of dataframe to ensure additional columns were dropped
len(movie_data)

260

This is a much more manageable number of calls to make to the API, so I stop the trimming here. There will be additional matching that needs to be done when the data frames are all combined in the last milestone (to account for duplicate titles, I will be merging on common keys release date and title), but for now this is a good amount of data to continue on gathering from the API.

### Pulling additional data from the API using the movie ID and merging data frames

The next API call has to be made by passing in a movie ID to the url. After the first API data retrieval, I now have IDs for all the movies in my data frame which I will use to make the next call and fetch some additional movie details,.

In [7]:
# Defining a function to fetch movie details from the API
def fetch_movie_details(movie_ids, api_key):
    # Constructing the base url
    url = 'https://api.themoviedb.org/3/movie/'
    # Creating an empty list to store movie data
    movie_details = []
    # Iterating over each movie ID
    for movie_id in movie_ids:
        # Constructing the full url by passing in movie ID and API key
        movie_url = f'{url}{movie_id}?api_key={api_key}'
        try:
            # Sending a get request tofetch data from API
            response = requests.get(movie_url)
            # Simple error handling - checking if response was successful
            if response.status_code == 200:
                # If response was successful, parse JSON data
                movie_data = response.json()
                
                # The following columns need some further JSON parsing as they return a list of dictionaries within the dataframe cell
                # Converting genres to comma-separated string
                movie_data['genres'] = ', '.join([genre['name'] for genre in movie_data.get('genres', [])])
                
                # Converting spoken_languages to comma-separated string
                movie_data['spoken_languages'] = ', '.join([lang['name'] for lang in movie_data.get('spoken_languages', [])])
                
                # Converting production_countries to comma-separated string
                movie_data['production_countries'] = ', '.join([country['name'] for country in movie_data.get('production_countries', [])])
                
                # Converting production_countries to comma-separated string
                movie_data['production_companies'] = ', '.join([company['name'] for company in movie_data.get('production_companies', [])])
                
                # Extracting the name of the collection to which the movie belongs if there is one
                belongs_to_collection = movie_data.get('belongs_to_collection')
                if belongs_to_collection:
                    movie_data['belongs_to_collection'] = belongs_to_collection.get('name', '')
                    
                # Appending movie data to the list
                movie_details.append(movie_data)
            # If data was not retrieved, print a message showing which movie data wasn't retrieved for
            else:
                print(f"Failed to retrieve data for movie ID {movie_id}")
        # If response was not received, print error that was encountered
        except Exception as e:
            print(f"An error occurred while processing movie ID {movie_id}: {e}")
    # Return movie_details list
    return movie_details


# Seperating API calls into batches of 50 to better limit calls to API
batch_size = 50

# Splitting the movie IDs into batches
movie_ids_batches = [movie_data['id'].iloc[i:i+batch_size] for i in range(0, len(movie_data), batch_size)]

# Creating a list to store data from each batch
additional_details = []

# Looping through each batch of movie IDs and fetch additional details
for batch_index, movie_ids_batch in enumerate(movie_ids_batches):
    # Printing current batch being processed to track progress
    print(f"Processing batch {batch_index+1} out of {len(movie_ids_batches)}")
    # Using fetch_movie_details on current batch
    batch_details = fetch_movie_details(movie_ids_batch, API_KEY)
    # Extending additional_details list with each batch
    additional_details.extend(batch_details)

# Converting the list of dictionaries from the JSON data into a data frame
additional_details_df = pd.DataFrame(additional_details)

# Displaying the data frame
display(additional_details_df)

Processing batch 1 out of 6
Processing batch 2 out of 6
Processing batch 3 out of 6
Processing batch 4 out of 6
Processing batch 5 out of 6
Processing batch 6 out of 6


adult                     backdrop_path  \
0    False  /6hgItrYQEG33y0I7yP2SRl2ei4w.jpg   
1    False   /BjLgTDAcZc94KomcQAxMVye0yI.jpg   
2    False  /xK5l1CMj4HllYfgCcOngC86E4o1.jpg   
3    False                              None   
4    False                              None   
5    False  /nC86jat6h6WxlQeCRyZIQAjjCsb.jpg   
6    False                              None   
7    False                              None   
8    False                              None   
9    False                              None   
10   False  /qlWUOd19T8qfzFSY5oUkppzNq24.jpg   
11   False                              None   
12   False  /nj84vpuUWdbmYktBzjiWn5Ny1ZF.jpg   
13   False                              None   
14   False  /1qDDU5kQUG3NwahbrUIXJcW36wu.jpg   
15   False  /cqcA0UeUFAajsd1XSpqGfqyqQN9.jpg   
16   False  /uCAy0n0WHTGU4d3LMJtE0fQxCej.jpg   
17   False  /2nLOJ8gtattGzYzwlYM8PrcgknH.jpg   
18   False  /lm4xH0YwFbVvTgdtau1thNK5S6J.jpg   
19   False  /5n2jz145P1CRdPfA296MmEZF1sQ.jpg   
20   False  /s3FDBLH4qc1IcjexB05Qvbn3wxO.jpg   
21   False  /m03jul0YdVEOFXEQVUv6pOVQYGL.jpg   
22   False  /2vJewgdaf0N8BnAgHZ8R7y3w5qQ.jpg   
23   False  /eZwwJ5yRpMDhZzfMS7XeWwUzLSE.jpg   
24   False  /cdMfn0Jr9RGqKkaX9HyR5l1kiYy.jpg   
25   False  /gJqQxpe03aIRZZjy8A4nbLtBpch.jpg   
26   False                              None   
27   False  /7KuGLqB3NcK0WPiDsfrUwrOqzDe.jpg   
28   False  /14HPHJnNUVAdbYKnG46WnBh4OD6.jpg   
29   False  /2ldAA1P4byx3aUdKDBT4mmSwYsK.jpg   
30   False                              None   
31   False  /gqemVzi13T4oB95EBufIxqafSCl.jpg   
32   False  /um7DVcGyLvImgAdn5JGpjIudYSV.jpg   
33   False  /jezUWimW5N3UXxatreKZ1oKjieN.jpg   
34   False  /c5cSnEIGFlhNuqtzCZuZTVlL1xX.jpg   
35   False                              None   
36   False  /sSalNFInZxGi0bmmIKJoDz5jI6n.jpg   
37   False  /owTL741kAuvJDKYnXKJCgTRGRud.jpg   
38   False  /zogWnCSztU8xvabaepQnAwsOtOt.jpg   
39   False  /oaOZ3EavXCBKXnkNoVTVZykmoOD.jpg   
40   False  /l3ViFvQq7903baibzhIGjowakHE.jpg   
41   False  /z2uuQasY4gQJ8VDAFki746JWeQJ.jpg   
42   False  /qLYtITl4Yrl9G9yYcFA2D6b61gh.jpg   
43   False  /kH8xW7K2Gp1KOXoeewcLPkfqZ8K.jpg   
44   False   /UxGdlGzCx5R5FdY8BDM0FQkyKi.jpg   
45   False  /gWsseHW73OOKvmZFoAff91xgj09.jpg   
46   False  /7XM7kxa3U2g8TO3OGSiETCroNRD.jpg   
47   False  /64jAqTJvrzEwncD3ARZdqYLcqbc.jpg   
48   False                              None   
49   False  /gKHPnH81jPIpCuvO3FgOkLbBV7C.jpg   
50   False                              None   
51   False                              None   
52   False                              None   
53   False                              None   
54   False   /2M2JxEv3HSpjnZWjY9NOdGgfUd.jpg   
55   False  /t7nUJ8aLDkGejeLiqrGCN3OGmnD.jpg   
56   False  /vy5bKKjcdws80nF9xSCeuXqOyuL.jpg   
57   False  /sJspZTaLdaoiQcy5S5ZWcQkLLGM.jpg   
58   False  /uF4gCZHiui3UJ2BzUb8Nr6De6Lt.jpg   
59   False  /nvk5PWrN74icx8pprK177OToj2b.jpg   
60   False  /n0FzDpOvVhkj3uN7WHXXnAXOKFi.jpg   
61   False  /1CpOFqgxOFOL2MxTWcIRfg6axy4.jpg   
62   False  /9lropttr13U34csVkseFGZY98Kl.jpg   
63   False  /sLTe3l1SX2h7xjfO0vwKhoQm3hx.jpg   
64   False  /rcUcYzGGicDvhDs58uM44tJKB9F.jpg   
65   False  /czJ2mC7fMhh4rRJ5UPaKb7fkKqo.jpg   
66   False  /vxlJveSEcEtmkcruQa3wB01ucnm.jpg   
67   False                              None   
68   False  /uLivGJgrChOg8VZCuJ7CzmGTsUV.jpg   
69   False  /ski23zB5ovZ3lf1ZPtOCIWDWoy6.jpg   
70   False  /fIRPoIFQsAlv78P6l178cRHWFcT.jpg   
71   False  /r2KizAu6OiGlQUE3qAkWR9BJCom.jpg   
72   False  /b6ZJZHUdMEFECvGiDpJjlfUWela.jpg   
73   False  /6K74rGGGjKGrblGTa7S9yRcUtnF.jpg   
74   False  /6XWp8sziGp8JG64mfRBAFjrUCxd.jpg   
75   False  /2shn4Kiq7qInZgKZhqM5BKie1zL.jpg   
76   False  /yR6952VuJ2OchliEj0vyRxFZiBT.jpg   
77   False                              None   
78   False  /8yE6wv1l570zWyh6zmkFxysw3Kc.jpg   
79   False  /htbWYT0oQDsttfs8LLmz8I2pbve.jpg   
80   False  /997ToEZvF2Obp9zNZbY5ELVnmrW.jpg   
81   False  /ckC6rzpaTH50alyzxPl2fBjgL1g.jpg   
82   False           

Now that this data fetch was successful, I will go ahead and merge the two data frames into a single data frame:

#### Merging the movie_data and additional_details_df frames along common key movie ID

In [8]:
# Merging the data frames based on the common key movie ID
movie_data = pd.merge(movie_data, additional_details_df, on='id', how='inner')
# Displaying merged data frame
display(movie_data)

adult_x                   backdrop_path_x                genre_ids  \
0      False  /6hgItrYQEG33y0I7yP2SRl2ei4w.jpg              [10749, 18]   
1      False   /BjLgTDAcZc94KomcQAxMVye0yI.jpg              [10749, 18]   
2      False  /xK5l1CMj4HllYfgCcOngC86E4o1.jpg                 [53, 18]   
3      False                              None                     [18]   
4      False                              None                       []   
5      False  /nC86jat6h6WxlQeCRyZIQAjjCsb.jpg                  [10402]   
6      False                              None                [878, 18]   
7      False                              None                       []   
8      False                              None                       []   
9      False                              None                     [18]   
10     False  /qlWUOd19T8qfzFSY5oUkppzNq24.jpg                  [10402]   
11     False                              None                     [99]   
12     False  /nj84vpuUWdbmYktBzjiWn5Ny1ZF.jpg                     [18]   
13     False                              None                     [18]   
14     False  /1qDDU5kQUG3NwahbrUIXJcW36wu.jpg                     [18]   
15     False  /cqcA0UeUFAajsd1XSpqGfqyqQN9.jpg                     [99]   
16     False  /uCAy0n0WHTGU4d3LMJtE0fQxCej.jpg      [10751, 16, 35, 14]   
17     False  /2nLOJ8gtattGzYzwlYM8PrcgknH.jpg             [28, 53, 18]   
18     False  /lm4xH0YwFbVvTgdtau1thNK5S6J.jpg             [53, 27, 28]   
19     False  /5n2jz145P1CRdPfA296MmEZF1sQ.jpg                     [18]   
20     False  /s3FDBLH4qc1IcjexB05Qvbn3wxO.jpg             [28, 80, 53]   
21     False  /m03jul0YdVEOFXEQVUv6pOVQYGL.jpg      [16, 35, 10751, 14]   
22     False  /2vJewgdaf0N8BnAgHZ8R7y3w5qQ.jpg                [35, 878]   
23     False  /eZwwJ5yRpMDhZzfMS7XeWwUzLSE.jpg          [18, 28, 10752]   
24     False  /cdMfn0Jr9RGqKkaX9HyR5l1kiYy.jpg                 [53, 18]   
25     False  /gJqQxpe03aIRZZjy8A4nbLtBpch.jpg       [80, 18, 9648, 53]   
26     False                              None                     [18]   
27     False  /7KuGLqB3NcK0WPiDsfrUwrOqzDe.jpg             [99, 36, 18]   
28     False  /14HPHJnNUVAdbYKnG46WnBh4OD6.jpg                 [28, 53]   
29     False  /2ldAA1P4byx3aUdKDBT4mmSwYsK.jpg             [53, 36, 18]   
30     False                              None                       []   
31     False  /gqemVzi13T4oB95EBufIxqafSCl.jpg             [28, 35, 80]   
32     False  /um7DVcGyLvImgAdn5JGpjIudYSV.jpg                 [18, 36]   
33     False  /jezUWimW5N3UXxatreKZ1oKjieN.jpg                     [99]   
34     False  /c5cSnEIGFlhNuqtzCZuZTVlL1xX.jpg           [27, 9648, 53]   
35     False                              None                     [18]   
36     False  /sSalNFInZxGi0bmmIKJoDz5jI6n.jpg              [10749, 18]   
37     False  /owTL741kAuvJDKYnXKJCgTRGRud.jpg            [27, 53, 878]   
38     False  /zogWnCSztU8xvabaepQnAwsOtOt.jpg             [28, 80, 18]   
39     False  /oaOZ3EavXCBKXnkNoVTVZykmoOD.jpg                     [18]   
40     False  /l3ViFvQq7903baibzhIGjowakHE.jpg                     [18]   
41     False  /z2uuQasY4gQJ8VDAFki746JWeQJ.jpg                 [99, 12]   
42     False  /qLYtITl4Yrl9G9yYcFA2D6b61gh.jpg         [53, 36, 18, 28]   
43     False  /kH8xW7K2Gp1KOXoeewcLPkfqZ8K.jpg                 [80, 18]   
44     False   /UxGdlGzCx5R5FdY8BDM0FQkyKi.jpg      [12, 16, 35, 10751]   
45     False  /gWsseHW73OOKvmZFoAff91xgj09.jpg              [99, 10402]   
46     False  /7XM7kxa3U2g8TO3OGSiETCroNRD.jpg              [35, 10749]   
47     False  /64jAqTJvrzEwncD3ARZdqYLcqbc.jpg          [53, 10749, 12]   
48     False                              None                     [99]   
49     False  /gKHPnH81jPIpCuvO3FgOkLbBV7C.jpg                     [18]   
50     False                              None                     [18]   
51     False                              None                       []   
52     False                  

Now that I have all the data I was looking for from the API, I can continue my cleaning steps.

#### Step 3: Removing unnecessary columns after merge

Merging the data frames left me with both duplicate columns and columns that I do not really need (such as genre IDs since I was able to parse out the genres). I am going to drop any unnecessary columns.

In [9]:
# Creating a list of columns to drop
columns_to_drop = ['genre_ids', 'adult_y', 'backdrop_path_y', 'original_language_y', 'original_title_y', 'overview_y', 
                   'popularity_y', 'poster_path_y', 'release_date_y', 'title_y', 'video_y', 'vote_average_y', 'vote_count_y']
# Using .drop() to drop the columns in the list
movie_data = movie_data.drop(columns = columns_to_drop)

In [10]:
# Checking to make sure columns were dropped
movie_data.head()

adult_x                   backdrop_path_x       id original_language_x  \
0    False  /6hgItrYQEG33y0I7yP2SRl2ei4w.jpg   613504                  en   
1    False   /BjLgTDAcZc94KomcQAxMVye0yI.jpg   642208                  en   
2    False  /xK5l1CMj4HllYfgCcOngC86E4o1.jpg   632455                  pl   
3    False                              None  1179465                  en   
4    False                              None   925991                  pt   

    original_title_x                                         overview_x  \
0  After We Collided  Tessa finds herself struggling with her compli...   
1          Supernova  Sam and Tusker, partners of 20 years, are trav...   
2          Supernova  Three men, one place and one event that will c...   
3          Supernova  On an awkward day on the beach, Hannah tries t...   
4          Supernova                                                      

   popularity_x                     poster_path_x release_date_x  \
0        74.446  /kiX7UYfOpYrMFSAGbI6j1pFkLzQ.jpg     2020-09-02   
1        15.737  /xpLi04zHu36TH8nuvFAwAF3LUkq.jpg     2020-11-20   
2         3.302  /xWDiMDQtNNsPAr3ANsQU2SVno6j.jpg     2019-11-22   
3         0.600                              None     2023-09-22   
4         0.600  /AbVuOfwlYeViMouqCrr6nJiEuuI.jpg     2018-08-15   

             title_x video_x  vote_average_x  vote_count_x  \
0  After We Collided   False           7.195        5157.0   
1          Supernova   False           7.000         291.0   
2          Supernova   False           6.891          22.0   
3          Supernova   False           6.000           1.0   
4          Supernova    True           0.000           0.0   

  belongs_to_collection    budget           genres  \
0      After Collection  14000000   Romance, Drama   
1                  None         0   Romance, Drama   
2                  None         0  Thriller, Drama   
3                  None         0            Drama   
4                  None         0                    

                                homepage     imdb_id  \
0                                         tt10362466   
1                                         tt11169050   
2  https://supernova-film.pl/movies/9922  tt10666454   
3                                               None   
4                                               None   

                                production_companies  \
0  Voltage Pictures, Offspring Entertainment, Fra...   
1               Quiddity Films, The Bureau, BBC Film   
2   Canal+ Polska, Stowarzyszenie Filmowców Polskich   
3                                                      
4                                                      

       production_countries   revenue  runtime spoken_languages    status  \
0  United States of America  48000000      105          English  Released   
1            United Kingdom   2506542       94          English  Released   
2                    Poland         0       78           Polski  Released   
3                                   0       12          English  Released   
4                    Brazil         0        0                   Released   

                                  tagline  
0             Can love overcome the past?  
1                                          
2  One moment can change your entire life  
3                                          
4

#### Step 4: Renaming columns

The column names are also quite messsy noe so I am going to replace them to make the data frame easier to work with:

In [11]:
# Creating a dictionary of column mapping, mapping original headers to new headers
column_mapping = {
    'adult_x': 'adult',
    'backdrop_path_x': 'backdrop_path',
    'id': 'id_tmdb',
    'original_language_x': 'original_language',
    'original_title_x': 'original_title',
    'overview_x': 'overview',
    'popularity_x': 'popularity',
    'poster_path_x': 'poster_path',
    'release_date_x': 'release_date_tmdb',
    'title_x': 'title',
    'video_x': 'video',
    'vote_average_x': 'vote_average',
    'vote_count_x': 'vote_count',
}

In [12]:
# Renaming the columns using .rename()
movie_data.rename(columns=column_mapping, inplace=True)
# Checking to make sure columns were renamed
movie_data.head()

adult                     backdrop_path  id_tmdb original_language  \
0  False  /6hgItrYQEG33y0I7yP2SRl2ei4w.jpg   613504                en   
1  False   /BjLgTDAcZc94KomcQAxMVye0yI.jpg   642208                en   
2  False  /xK5l1CMj4HllYfgCcOngC86E4o1.jpg   632455                pl   
3  False                              None  1179465                en   
4  False                              None   925991                pt   

      original_title                                           overview  \
0  After We Collided  Tessa finds herself struggling with her compli...   
1          Supernova  Sam and Tusker, partners of 20 years, are trav...   
2          Supernova  Three men, one place and one event that will c...   
3          Supernova  On an awkward day on the beach, Hannah tries t...   
4          Supernova                                                      

   popularity                       poster_path release_date_tmdb  \
0      74.446  /kiX7UYfOpYrMFSAGbI6j1pFkLzQ.jpg        2020-09-02   
1      15.737  /xpLi04zHu36TH8nuvFAwAF3LUkq.jpg        2020-11-20   
2       3.302  /xWDiMDQtNNsPAr3ANsQU2SVno6j.jpg        2019-11-22   
3       0.600                              None        2023-09-22   
4       0.600  /AbVuOfwlYeViMouqCrr6nJiEuuI.jpg        2018-08-15   

               title  video  vote_average  vote_count belongs_to_collection  \
0  After We Collided  False         7.195      5157.0      After Collection   
1          Supernova  False         7.000       291.0                  None   
2          Supernova  False         6.891        22.0                  None   
3          Supernova  False         6.000         1.0                  None   
4          Supernova   True         0.000         0.0                  None   

     budget           genres                               homepage  \
0  14000000   Romance, Drama                                          
1         0   Romance, Drama                                          
2         0  Thriller, Drama  https://supernova-film.pl/movies/9922   
3         0            Drama                                          
4         0                                                           

      imdb_id                               production_companies  \
0  tt10362466  Voltage Pictures, Offspring Entertainment, Fra...   
1  tt11169050               Quiddity Films, The Bureau, BBC Film   
2  tt10666454   Canal+ Polska, Stowarzyszenie Filmowców Polskich   
3        None                                                      
4        None                                                      

       production_countries   revenue  runtime spoken_languages    status  \
0  United States of America  48000000      105          English  Released   
1            United Kingdom   2506542       94          English  Released   
2                    Poland         0       78           Polski  Released   
3                                   0       12          English  Released   
4                    Brazil         0        0                   Released   

                                  tagline  
0             Can love overcome the past?  
1                                          
2  One moment can change your entire life  
3                                          
4

#### Step 5: Replacing 0s in certian columns with NaN

The columns budget, runtime, and revenue all have a number of rows with 0s entered. However, it doesn't make sense to have a film with a budget or runtime of 0, and it is unlikely that a film made no money, so more than likely there is just not data associated with certain films for these columns. I want to change these 0s to NaNs so as not to throw off any potential future analyses.

In [13]:
movie_data['budget'] = movie_data['budget'].replace(0, np.nan)
movie_data['revenue'] = movie_data['revenue'].replace(0, np.nan)
movie_data['runtime'] = movie_data['runtime'].replace(0, np.nan)

display(movie_data)

adult                     backdrop_path  id_tmdb original_language  \
0    False  /6hgItrYQEG33y0I7yP2SRl2ei4w.jpg   613504                en   
1    False   /BjLgTDAcZc94KomcQAxMVye0yI.jpg   642208                en   
2    False  /xK5l1CMj4HllYfgCcOngC86E4o1.jpg   632455                pl   
3    False                              None  1179465                en   
4    False                              None   925991                pt   
5    False  /nC86jat6h6WxlQeCRyZIQAjjCsb.jpg   919678                en   
6    False                              None  1162706                de   
7    False                              None   641317                fr   
8    False                              None   926891                en   
9    False                              None  1213722                fr   
10   False  /qlWUOd19T8qfzFSY5oUkppzNq24.jpg  1194370                pt   
11   False                              None  1218923                en   
12   False  /nj84vpuUWdbmYktBzjiWn5Ny1ZF.jpg   525661                en   
13   False                              None  1121661                en   
14   False  /1qDDU5kQUG3NwahbrUIXJcW36wu.jpg   443463                en   
15   False  /cqcA0UeUFAajsd1XSpqGfqyqQN9.jpg   965398                en   
16   False  /uCAy0n0WHTGU4d3LMJtE0fQxCej.jpg   481084                en   
17   False  /2nLOJ8gtattGzYzwlYM8PrcgknH.jpg   399248                en   
18   False  /lm4xH0YwFbVvTgdtau1thNK5S6J.jpg   511987                en   
19   False  /5n2jz145P1CRdPfA296MmEZF1sQ.jpg   512263                en   
20   False  /s3FDBLH4qc1IcjexB05Qvbn3wxO.jpg   449443                en   
21   False  /m03jul0YdVEOFXEQVUv6pOVQYGL.jpg   400155                en   
22   False  /2vJewgdaf0N8BnAgHZ8R7y3w5qQ.jpg   653569                en   
23   False  /eZwwJ5yRpMDhZzfMS7XeWwUzLSE.jpg   442065                en   
24   False  /cdMfn0Jr9RGqKkaX9HyR5l1kiYy.jpg   510298                en   
25   False  /gJqQxpe03aIRZZjy8A4nbLtBpch.jpg   401545                es   
26   False                              None  1158818                he   
27   False  /7KuGLqB3NcK0WPiDsfrUwrOqzDe.jpg   549559                en   
28   False  /14HPHJnNUVAdbYKnG46WnBh4OD6.jpg   458594                en   
29   False  /2ldAA1P4byx3aUdKDBT4mmSwYsK.jpg   615115                en   
30   False                              None   853806                es   
31   False  /gqemVzi13T4oB95EBufIxqafSCl.jpg   412988                en   
32   False  /um7DVcGyLvImgAdn5JGpjIudYSV.jpg   454652                en   
33   False  /jezUWimW5N3UXxatreKZ1oKjieN.jpg   741845                fr   
34   False  /c5cSnEIGFlhNuqtzCZuZTVlL1xX.jpg   605804                en   
35   False                              None  1061811                en   
36   False  /sSalNFInZxGi0bmmIKJoDz5jI6n.jpg   710356                en   
37   False  /owTL741kAuvJDKYnXKJCgTRGRud.jpg   435615                en   
38   False  /zogWnCSztU8xvabaepQnAwsOtOt.jpg   531499                en   
39   False  /oaOZ3EavXCBKXnkNoVTVZykmoOD.jpg   535845                en   
40   False  /l3ViFvQq7903baibzhIGjowakHE.jpg   664297                en   
41   False  /z2uuQasY4gQJ8VDAFki746JWeQJ.jpg   515042                en   
42   False  /qLYtITl4Yrl9G9yYcFA2D6b61gh.jpg   416144                en   
43   False  /kH8xW7K2Gp1KOXoeewcLPkfqZ8K.jpg   470044                en   
44   False   /UxGdlGzCx5R5FdY8BDM0FQkyKi.jpg   412117                en   
45   False  /gWsseHW73OOKvmZFoAff91xgj09.jpg   549551                en   
46   False  /7XM7kxa3U2g8TO3OGSiETCroNRD.jpg   460668                en   
47   False  /64jAqTJvrzEwncD3ARZdqYLcqbc.jpg   429300                en   
48   False                              None  1170309                en   
49   False  /gKHPnH81jPIpCuvO3FgOkLbBV7C.jpg  1050304                en   
50   False                              None  1122440                en   
51   False                              None   619320                fr   
52   False                    

#### Step 6: Turning Genres into more usable data using get_dummies()

This data is in relatively good shape, however there is one last transformation I'd like to make: turning the genres column into more usable data. As it stands right now, all of a film's genres are crammed into a singular cell and seperated by a comma. In order to make analysis by genre easier, I am going to break that column out using get_dummies from pandas to create seperate columns for each genre and populating a 1 if the movie falls under that genre and a 0 if it does not.

In [14]:
# Converting the genres column into ddummy variables, using a comma as the separator
genre_dummies = movie_data['genres'].str.get_dummies(sep=', ')

# Renaming the dummy columns based on the genre type (ex, genre_Action)
genre_dummies.columns = ['genre_' + column for column in genre_dummies.columns]

# Concatenating the dummy variables onto the original data frame
movie_data = pd.concat([movie_data, genre_dummies], axis=1)

In [15]:
# Checking the data frame
movie_data.head()

adult                     backdrop_path  id_tmdb original_language  \
0  False  /6hgItrYQEG33y0I7yP2SRl2ei4w.jpg   613504                en   
1  False   /BjLgTDAcZc94KomcQAxMVye0yI.jpg   642208                en   
2  False  /xK5l1CMj4HllYfgCcOngC86E4o1.jpg   632455                pl   
3  False                              None  1179465                en   
4  False                              None   925991                pt   

      original_title                                           overview  \
0  After We Collided  Tessa finds herself struggling with her compli...   
1          Supernova  Sam and Tusker, partners of 20 years, are trav...   
2          Supernova  Three men, one place and one event that will c...   
3          Supernova  On an awkward day on the beach, Hannah tries t...   
4          Supernova                                                      

   popularity                       poster_path release_date_tmdb  \
0      74.446  /kiX7UYfOpYrMFSAGbI6j1pFkLzQ.jpg        2020-09-02   
1      15.737  /xpLi04zHu36TH8nuvFAwAF3LUkq.jpg        2020-11-20   
2       3.302  /xWDiMDQtNNsPAr3ANsQU2SVno6j.jpg        2019-11-22   
3       0.600                              None        2023-09-22   
4       0.600  /AbVuOfwlYeViMouqCrr6nJiEuuI.jpg        2018-08-15   

               title  video  vote_average  vote_count belongs_to_collection  \
0  After We Collided  False         7.195      5157.0      After Collection   
1          Supernova  False         7.000       291.0                  None   
2          Supernova  False         6.891        22.0                  None   
3          Supernova  False         6.000         1.0                  None   
4          Supernova   True         0.000         0.0                  None   

       budget           genres                               homepage  \
0  14000000.0   Romance, Drama                                          
1         NaN   Romance, Drama                                          
2         NaN  Thriller, Drama  https://supernova-film.pl/movies/9922   
3         NaN            Drama                                          
4         NaN                                                           

      imdb_id                               production_companies  \
0  tt10362466  Voltage Pictures, Offspring Entertainment, Fra...   
1  tt11169050               Quiddity Films, The Bureau, BBC Film   
2  tt10666454   Canal+ Polska, Stowarzyszenie Filmowców Polskich   
3        None                                                      
4        None                                                      

       production_countries     revenue  runtime spoken_languages    status  \
0  United States of America  48000000.0    105.0          English  Released   
1            United Kingdom   2506542.0     94.0          English  Released   
2                    Poland         NaN     78.0           Polski  Released   
3                                   NaN     12.0          English  Released   
4                    Brazil         NaN      NaN                   Released   

                                  tagline  genre_Action  genre_Adventure  \
0             Can love overcome the past?             0                0   
1                                                     0                0   
2  One moment can change your entire life             0                0   
3                                                     0                0   
4                                                     0                0   

   genre_Animation  genre_Comedy  genre_Crime  genre_Documentary  genre_Drama  \
0                0             0            0                  0            1   
1                0             0            0                  0            1   
2                0             0            0                  0            1   
3                0             0            0                  0            1   
4                0             0      

Now the genre data is in a much more usable format.

### Printing and Exporting the Final Data Set

In [16]:
# Displaying the final data set
display(movie_data)

adult                     backdrop_path  id_tmdb original_language  \
0    False  /6hgItrYQEG33y0I7yP2SRl2ei4w.jpg   613504                en   
1    False   /BjLgTDAcZc94KomcQAxMVye0yI.jpg   642208                en   
2    False  /xK5l1CMj4HllYfgCcOngC86E4o1.jpg   632455                pl   
3    False                              None  1179465                en   
4    False                              None   925991                pt   
5    False  /nC86jat6h6WxlQeCRyZIQAjjCsb.jpg   919678                en   
6    False                              None  1162706                de   
7    False                              None   641317                fr   
8    False                              None   926891                en   
9    False                              None  1213722                fr   
10   False  /qlWUOd19T8qfzFSY5oUkppzNq24.jpg  1194370                pt   
11   False                              None  1218923                en   
12   False  /nj84vpuUWdbmYktBzjiWn5Ny1ZF.jpg   525661                en   
13   False                              None  1121661                en   
14   False  /1qDDU5kQUG3NwahbrUIXJcW36wu.jpg   443463                en   
15   False  /cqcA0UeUFAajsd1XSpqGfqyqQN9.jpg   965398                en   
16   False  /uCAy0n0WHTGU4d3LMJtE0fQxCej.jpg   481084                en   
17   False  /2nLOJ8gtattGzYzwlYM8PrcgknH.jpg   399248                en   
18   False  /lm4xH0YwFbVvTgdtau1thNK5S6J.jpg   511987                en   
19   False  /5n2jz145P1CRdPfA296MmEZF1sQ.jpg   512263                en   
20   False  /s3FDBLH4qc1IcjexB05Qvbn3wxO.jpg   449443                en   
21   False  /m03jul0YdVEOFXEQVUv6pOVQYGL.jpg   400155                en   
22   False  /2vJewgdaf0N8BnAgHZ8R7y3w5qQ.jpg   653569                en   
23   False  /eZwwJ5yRpMDhZzfMS7XeWwUzLSE.jpg   442065                en   
24   False  /cdMfn0Jr9RGqKkaX9HyR5l1kiYy.jpg   510298                en   
25   False  /gJqQxpe03aIRZZjy8A4nbLtBpch.jpg   401545                es   
26   False                              None  1158818                he   
27   False  /7KuGLqB3NcK0WPiDsfrUwrOqzDe.jpg   549559                en   
28   False  /14HPHJnNUVAdbYKnG46WnBh4OD6.jpg   458594                en   
29   False  /2ldAA1P4byx3aUdKDBT4mmSwYsK.jpg   615115                en   
30   False                              None   853806                es   
31   False  /gqemVzi13T4oB95EBufIxqafSCl.jpg   412988                en   
32   False  /um7DVcGyLvImgAdn5JGpjIudYSV.jpg   454652                en   
33   False  /jezUWimW5N3UXxatreKZ1oKjieN.jpg   741845                fr   
34   False  /c5cSnEIGFlhNuqtzCZuZTVlL1xX.jpg   605804                en   
35   False                              None  1061811                en   
36   False  /sSalNFInZxGi0bmmIKJoDz5jI6n.jpg   710356                en   
37   False  /owTL741kAuvJDKYnXKJCgTRGRud.jpg   435615                en   
38   False  /zogWnCSztU8xvabaepQnAwsOtOt.jpg   531499                en   
39   False  /oaOZ3EavXCBKXnkNoVTVZykmoOD.jpg   535845                en   
40   False  /l3ViFvQq7903baibzhIGjowakHE.jpg   664297                en   
41   False  /z2uuQasY4gQJ8VDAFki746JWeQJ.jpg   515042                en   
42   False  /qLYtITl4Yrl9G9yYcFA2D6b61gh.jpg   416144                en   
43   False  /kH8xW7K2Gp1KOXoeewcLPkfqZ8K.jpg   470044                en   
44   False   /UxGdlGzCx5R5FdY8BDM0FQkyKi.jpg   412117                en   
45   False  /gWsseHW73OOKvmZFoAff91xgj09.jpg   549551                en   
46   False  /7XM7kxa3U2g8TO3OGSiETCroNRD.jpg   460668                en   
47   False  /64jAqTJvrzEwncD3ARZdqYLcqbc.jpg   429300                en   
48   False                              None  1170309                en   
49   False  /gKHPnH81jPIpCuvO3FgOkLbBV7C.jpg  1050304                en   
50   False                              None  1122440                en   
51   False                              None   619320                fr   
52   False                    

In [17]:
# Exporting to .csv
movie_data.to_csv('tmdb_data.csv', index=False)

### Ethical Considerations of this Data Wrangling

This was one of my first experiences working with data retrieved through an API, so I took extra caution to be mindful of where and how I was retrieving them data for this part of the project. First, the API I chose was Thhe Movie Database (TMDb), which is a reputable and well-established database for film and television shows. Upon choosing the API, I ensured that my intentions for the data and what I would be asking of the API adhered to the policies outlined by TMDb, and when requesting the API key I had to submit these intentions and be approved. For my initial API call, I used my previous data sets to make more targeted requests for data to limit the number of times I was sending requests to the API. By the second API call, I also learned how to send data requests in batches so as to not overload the API's servers by sending large numbers of requests all at once. While working with the data in my notebook, I was also mindful to not rerun the code blocks for making API calls unnecessarily to not clog up the servers as well, even though my calls were most likely relatively small. Working with an API taught me a lot about being respectful and transparent about how and foro what I am requesting the data for.

As for the data wrangling steps themselves, the only consideration I can see is in my step of changing 0s in revenue, budget, and runtime to NaNs. While runtime is fairly self explanatory (all films have at least some runtime, so it was safe to assume 0s meant bi runtime was a vailabel), I did make this same assumption for both budget and revenue. I assumed that all films, no matter how large or small, should have some type of budget or record of cost of resources allocated to the project, but it very well could be the case that there are films that were somehow created with no budget. My assumptions for revenue were along the similar vein, thought there very well could be films that were made and generated no revenue and could have truly been 0 in this field. However, I weighed the potential costs of losing a few of these data points with the benefits of ensuring that 0s were replaced with NaN to cover cases where the 0 truly just meant there was no data, and the benefits of handling these outliers at this point in my process outweighed the potential costs. 

Looking overall at my project, the biggest ethical consideration I am taking into account at this time is data representation. Once I retrieved common movie titles from my previous two data sets in order to make more targeted calls to the API for data, I realized that the data pulled from my web source was exclusive to the top performing films of each year. While this might give me a good data set to investigate common threads between monetarily successful films, it would also be beneficial to look at commonalities between films that didn't generate as much revenue, and looking ahead to the final milestone as my data stands now this may be an underrepresented group in my final merged data set. 